**Deep Learning Assignment 3: Python Code Notebook for Implementation of ResNet16 on Cancer CT Scan dataset**

**Author:** Srirupa Guha

**Date:** 16th June 2022

**Email id:** srirupaguha18@gmail.com

Mounting the Google Drive to load Covid dataset

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


**Imports**

In [ ]:
import cv2
import numpy as np
import shutil
import os
from keras.preprocessing.image import ImageDataGenerator
from keras import backend as K
import keras
from keras.models import Sequential, Model,load_model
from tensorflow.keras.optimizers import SGD
from keras.callbacks import EarlyStopping,ModelCheckpoint
from google.colab.patches import cv2_imshow
from keras.layers import Input, Add, Dense, Activation, ZeroPadding2D, BatchNormalization, Flatten, Conv2D, AveragePooling2D, MaxPooling2D, GlobalMaxPooling2D,MaxPool2D
from keras.preprocessing import image
from keras.initializers import glorot_uniform
import tensorflow as tf
from matplotlib import pyplot
import pandas as pd
import tensorflow as tf
from tensorflow import keras
from tensorflow.keras import backend
from tensorflow.keras.preprocessing.image import ImageDataGenerator
from tensorflow.keras.layers import Input, Conv2D, MaxPooling2D, GlobalAveragePooling2D, BatchNormalization
from tensorflow.keras.layers import Dense, Dropout, Flatten, Activation, Concatenate, Lambda
from tensorflow.keras.models import Model
from tensorflow.keras.callbacks import EarlyStopping, ReduceLROnPlateau, ModelCheckpoint
from tensorflow.keras.optimizers import Adam
from tensorflow.keras import regularizers, activations
import os
from sklearn.utils import shuffle
from sklearn.metrics import classification_report, confusion_matrix, roc_curve, auc
from sklearn.model_selection import train_test_split
import matplotlib.pyplot as plt
#import itertools
#import shutil
%matplotlib inline

In [ ]:
# folder path
benign_dir_path = r'/content/drive/MyDrive/Assignments/Assignment 3/Annotated_Cropped_Dataset/Benign/'
benign_image_count = 0
# Iterate directory
for path in os.listdir(benign_dir_path):
    # check if current path is a file
    if os.path.isfile(os.path.join(benign_dir_path, path)):
        benign_image_count += 1
print('File count:', benign_image_count)

File count: 3761


In [ ]:
# folder path
malignant_dir_path = r'/content/drive/MyDrive/Assignments/Assignment 3/Annotated_Cropped_Dataset/Malignant/'
malignant_image_count = 0
# Iterate directory
for path in os.listdir(malignant_dir_path):
    # check if current path is a file
    if os.path.isfile(os.path.join(malignant_dir_path, path)):
        malignant_image_count += 1
print('File count:', malignant_image_count)

File count: 1444


In [ ]:
# benign_train_size = 0.7*benign_image_count
# benign_val_size = 0.2*benign_image_count
# benign_test_size = 0.1*benign_image_count

# malignant_train_size = 0.7*malignant_image_count
# malignant_val_size = 0.2*malignant_image_count
# malignant_test_size = 0.1*malignant_image_count

In [ ]:
# benign_source_folder = '/content/drive/MyDrive/Assignments/Assignment 3/Annotated_Cropped_Dataset/Benign/'
# malignant_source_folder = '/content/drive/MyDrive/Assignments/Assignment 3/Annotated_Cropped_Dataset/Malignant/'

# train_benign_destination_folder = '/content/drive/MyDrive/Assignments/Assignment 3/Annotated_Cropped_Dataset_Training/Train/Benign/'
# train_malignant_destination_folder = '/content/drive/MyDrive/Assignments/Assignment 3/Annotated_Cropped_Dataset_Training/Train/Malignant/'

# val_benign_destination_folder = '/content/drive/MyDrive/Assignments/Assignment 3/Annotated_Cropped_Dataset_Training/Val/Benign/'
# val_malignant_destination_folder = '/content/drive/MyDrive/Assignments/Assignment 3/Annotated_Cropped_Dataset_Training/Val/Malignant/'

# test_benign_destination_folder = '/content/drive/MyDrive/Assignments/Assignment 3/Annotated_Cropped_Dataset_Training/Test/Benign/'
# test_malignant_destination_folder = '/content/drive/MyDrive/Assignments/Assignment 3/Annotated_Cropped_Dataset_Training/Test/Malignant/'

# #benign

# benign_count = 0

# for filename in os.listdir(benign_source_folder):
#     print(filename)

#     benign_count = benign_count + 1

#     if benign_count <= benign_train_size:
#       shutil.copy2(benign_source_folder + filename, train_benign_destination_folder + filename)

#     elif ((benign_count > benign_train_size) and (benign_count <= benign_train_size + benign_val_size + 1)):
#       shutil.copy(benign_source_folder + filename, val_benign_destination_folder + filename)

#     elif ((benign_count > benign_train_size + benign_val_size + 1) and (benign_count <= benign_train_size + benign_val_size + benign_test_size + 1)):
#       shutil.copy(benign_source_folder + filename, test_benign_destination_folder + filename)

# #malignant

# malignant_count = 0

# for filename in os.listdir(malignant_source_folder):
#     print(filename)

#     malignant_count = malignant_count + 1

#     if malignant_count <= malignant_train_size:
#       shutil.copy(malignant_source_folder + filename, train_malignant_destination_folder + filename)

#     elif ((malignant_count > malignant_train_size) and (malignant_count <= malignant_train_size + malignant_val_size + 1)):
#       shutil.copy(malignant_source_folder + filename, val_malignant_destination_folder + filename)

#     elif ((malignant_count > malignant_train_size + malignant_val_size + 1) and (malignant_count <= malignant_train_size + malignant_val_size + malignant_test_size + 1)):
#       shutil.copy(malignant_source_folder + filename, test_malignant_destination_folder + filename)

In [ ]:
# train_path="/content/drive/MyDrive/Assignments/Assignment 3/Annotated_Cropped_Dataset_Training/Train/"
# val_path="/content/drive/MyDrive/Assignments/Assignment 3/Annotated_Cropped_Dataset_Training/Val/"
# test_path="/content/drive/MyDrive/Assignments/Assignment 3/Annotated_Cropped_Dataset_Training/Test/"
# class_names=os.listdir(train_path)
# class_names_val=os.listdir(val_path)
# class_names_test=os.listdir(test_path)

# print(class_names)
# print(class_names_test)

In [ ]:
# #Sample datasets images

# image_Benign =cv2.imread("/content/drive/MyDrive/Assignments/Assignment 3/Custom_Dataset/Train/Benign/01.jpg")
# imS1 = cv2.resize(image_Benign, (100, 100))
# cv2_imshow(imS1)
# image_Malignant=cv2.imread("/content/drive/MyDrive/Assignments/Assignment 3/Custom_Dataset/Train/Malignant/03.jpg")
# imS2 = cv2.resize(image_Malignant, (100, 100))
# cv2_imshow(imS2)

In [ ]:
# train_datagen = ImageDataGenerator(zoom_range=0.15,width_shift_range=0.2,height_shift_range=0.2,shear_range=0.15)
# val_datagen = ImageDataGenerator()
# test_datagen = ImageDataGenerator()

In [ ]:
# train_generator = train_datagen.flow_from_directory("/content/drive/MyDrive/Assignments/Assignment 3/Model_Training_Dataset/Train/",target_size=(224, 224),batch_size=32,shuffle=True,class_mode='binary')
# val_generator = val_datagen.flow_from_directory("/content/drive/MyDrive/Assignments/Assignment 3/Model_Training_Dataset/Val/",target_size=(224,224),batch_size=32,shuffle=False,class_mode='binary')
# test_generator = test_datagen.flow_from_directory("/content/drive/MyDrive/Assignments/Assignment 3/Model_Training_Dataset/Test/",target_size=(224,224),batch_size=32,shuffle=False,class_mode='binary')

In [ ]:
import os

train_benign_list = os.listdir("/content/drive/MyDrive/Assignments/Assignment 3/Model_Training_Dataset/Train/Benign") # dir is your directory path
train_benign_number_files = len(train_benign_list)
train_benign_number_files

2633

In [ ]:
train_malignant_list = os.listdir("/content/drive/MyDrive/Assignments/Assignment 3/Model_Training_Dataset/Train/Malignant") # dir is your directory path
train_malignant_number_files = len(train_malignant_list)
train_malignant_number_files

1011

In [ ]:
val_benign_list = os.listdir("/content/drive/MyDrive/Assignments/Assignment 3/Model_Training_Dataset/Val/Benign") # dir is your directory path
val_benign_number_files = len(val_benign_list)
val_benign_number_files

1128

In [ ]:
val_malignant_list = os.listdir("/content/drive/MyDrive/Assignments/Assignment 3/Model_Training_Dataset/Val/Malignant") # dir is your directory path
val_malignant_number_files = len(val_malignant_list)
val_malignant_number_files

433

In [ ]:
test_benign_list = os.listdir("/content/drive/MyDrive/Assignments/Assignment 3/Model_Training_Dataset/Test/Benign") # dir is your directory path
test_benign_number_files = len(test_benign_list)
test_benign_number_files

376

In [ ]:
test_malignant_list = os.listdir("/content/drive/MyDrive/Assignments/Assignment 3/Model_Training_Dataset/Test/Malignant") # dir is your directory path
test_malignant_number_files = len(test_malignant_list)
test_malignant_number_files

144

**Defining functions for conv2d, inception-ResA, inception-ResB, Iinception-resC, stem blacks and the inception-resnet network**

**Convolutional Block**

In [ ]:
def conv2d(x,numfilt,filtsz,strides=1,pad='same',act=True,name=None):
  x = Conv2D(numfilt,filtsz,strides,padding=pad,data_format='channels_last',use_bias=False,name=name+'conv2d')(x)
  x = BatchNormalization(axis=3,scale=False,name=name+'conv2d'+'bn')(x)
  if act:
    x = Activation('relu',name=name+'conv2d'+'act')(x)
  return x

**Inception ResNet A block**

In [ ]:
def incresA(x,scale,name=None):
    pad = 'same'
    branch0 = conv2d(x,32,1,1,pad,True,name=name+'b0')
    branch1 = conv2d(x,32,1,1,pad,True,name=name+'b1_1')
    branch1 = conv2d(branch1,32,3,1,pad,True,name=name+'b1_2')
    branch2 = conv2d(x,32,1,1,pad,True,name=name+'b2_1')
    branch2 = conv2d(branch2,48,3,1,pad,True,name=name+'b2_2')
    branch2 = conv2d(branch2,64,3,1,pad,True,name=name+'b2_3')
    branches = [branch0,branch1,branch2]
    mixed = Concatenate(axis=3, name=name + '_concat')(branches)
    filt_exp_1x1 = conv2d(mixed,384,1,1,pad,False,name=name+'filt_exp_1x1')
    final_lay = Lambda(lambda inputs, scale: inputs[0] + inputs[1] * scale,
                      output_shape=backend.int_shape(x)[1:],
                      arguments={'scale': scale},
                      name=name+'act_scaling')([x, filt_exp_1x1])
    return final_lay

**Inception ResNet B block**

In [ ]:
def incresB(x,scale,name=None):
    pad = 'same'
    branch0 = conv2d(x,192,1,1,pad,True,name=name+'b0')
    branch1 = conv2d(x,128,1,1,pad,True,name=name+'b1_1')
    branch1 = conv2d(branch1,160,[1,7],1,pad,True,name=name+'b1_2')
    branch1 = conv2d(branch1,192,[7,1],1,pad,True,name=name+'b1_3')
    branches = [branch0,branch1]
    mixed = Concatenate(axis=3, name=name + '_mixed')(branches)
    filt_exp_1x1 = conv2d(mixed,1152,1,1,pad,False,name=name+'filt_exp_1x1')
    final_lay = Lambda(lambda inputs, scale: inputs[0] + inputs[1] * scale,
                      output_shape=backend.int_shape(x)[1:],
                      arguments={'scale': scale},
                      name=name+'act_scaling')([x, filt_exp_1x1])
    return final_lay

**Inception ResNet C block**

In [ ]:
def incresC(x,scale,name=None):
    pad = 'same'
    branch0 = conv2d(x,192,1,1,pad,True,name=name+'b0')
    branch1 = conv2d(x,192,1,1,pad,True,name=name+'b1_1')
    branch1 = conv2d(branch1,224,[1,3],1,pad,True,name=name+'b1_2')
    branch1 = conv2d(branch1,256,[3,1],1,pad,True,name=name+'b1_3')
    branches = [branch0,branch1]
    mixed = Concatenate(axis=3, name=name + '_mixed')(branches)
    filt_exp_1x1 = conv2d(mixed,2048,1,1,pad,False,name=name+'fin1x1')
    final_lay = Lambda(lambda inputs, scale: inputs[0] + inputs[1] * scale,
                      output_shape=backend.int_shape(x)[1:],
                      arguments={'scale': scale},
                      name=name+'act_saling')([x, filt_exp_1x1])
    return final_lay

**Stem block**

In [ ]:
img_input = Input(shape=(256,256,3))

x = conv2d(img_input,32,3,2,'valid',True,name='conv1')
x = conv2d(x,32,3,1,'valid',True,name='conv2')
x = conv2d(x,64,3,1,'valid',True,name='conv3')

x_11 = MaxPooling2D(3,strides=1,padding='valid',name='stem_br_11'+'_maxpool_1')(x)
x_12 = conv2d(x,64,3,1,'valid',True,name='stem_br_12')

x = Concatenate(axis=3, name = 'stem_concat_1')([x_11,x_12])

x_21 = conv2d(x,64,1,1,'same',True,name='stem_br_211')
x_21 = conv2d(x_21,64,[1,7],1,'same',True,name='stem_br_212')
x_21 = conv2d(x_21,64,[7,1],1,'same',True,name='stem_br_213')
x_21 = conv2d(x_21,96,3,1,'valid',True,name='stem_br_214')

x_22 = conv2d(x,64,1,1,'same',True,name='stem_br_221')
x_22 = conv2d(x_22,96,3,1,'valid',True,name='stem_br_222')

x = Concatenate(axis=3, name = 'stem_concat_2')([x_21,x_22])

x_31 = conv2d(x,192,3,1,'valid',True,name='stem_br_31')
x_32 = MaxPooling2D(3,strides=1,padding='valid',name='stem_br_32'+'_maxpool_2')(x)
x = Concatenate(axis=3, name = 'stem_concat_3')([x_31,x_32])

**Inception-ResNet Network**

In [ ]:
num_classes = 2

#Inception-ResNet-A modules
x = incresA(x,0.15,name='incresA_1')
x = incresA(x,0.15,name='incresA_2')
x = incresA(x,0.15,name='incresA_3')
x = incresA(x,0.15,name='incresA_4')

#35 × 35 to 17 × 17 reduction module.
x_red_11 = MaxPooling2D(3,strides=2,padding='valid',name='red_maxpool_1')(x)

x_red_12 = conv2d(x,384,3,2,'valid',True,name='x_red1_c1')

x_red_13 = conv2d(x,256,1,1,'same',True,name='x_red1_c2_1')
x_red_13 = conv2d(x_red_13,256,3,1,'same',True,name='x_red1_c2_2')
x_red_13 = conv2d(x_red_13,384,3,2,'valid',True,name='x_red1_c2_3')

x = Concatenate(axis=3, name='red_concat_1')([x_red_11,x_red_12,x_red_13])

#Inception-ResNet-B modules
x = incresB(x,0.1,name='incresB_1')
x = incresB(x,0.1,name='incresB_2')
x = incresB(x,0.1,name='incresB_3')
x = incresB(x,0.1,name='incresB_4')
x = incresB(x,0.1,name='incresB_5')
x = incresB(x,0.1,name='incresB_6')
x = incresB(x,0.1,name='incresB_7')

#17 × 17 to 8 × 8 reduction module.
x_red_21 = MaxPooling2D(3,strides=2,padding='valid',name='red_maxpool_2')(x)

x_red_22 = conv2d(x,256,1,1,'same',True,name='x_red2_c11')
x_red_22 = conv2d(x_red_22,384,3,2,'valid',True,name='x_red2_c12')

x_red_23 = conv2d(x,256,1,1,'same',True,name='x_red2_c21')
x_red_23 = conv2d(x_red_23,256,3,2,'valid',True,name='x_red2_c22')

x_red_24 = conv2d(x,256,1,1,'same',True,name='x_red2_c31')
x_red_24 = conv2d(x_red_24,256,3,1,'same',True,name='x_red2_c32')
x_red_24 = conv2d(x_red_24,256,3,2,'valid',True,name='x_red2_c33')

x = Concatenate(axis=3, name='red_concat_2')([x_red_21,x_red_22,x_red_23,x_red_24])

#Inception-ResNet-C modules
x = incresC(x,0.2,name='incresC_1')
x = incresC(x,0.2,name='incresC_2')
x = incresC(x,0.2,name='incresC_3')

#TOP
x = GlobalAveragePooling2D(data_format='channels_last')(x)
x = Dropout(0.6)(x)
x = Dense(num_classes, activation='softmax')(x)

**Model Summary**

In [ ]:
model = Model(img_input,x,name='inception_resnet_v2')

In [ ]:
model.summary()

Model: "inception_resnet_v2"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 input_1 (InputLayer)           [(None, 256, 256, 3  0           []                               
                                )]                                                                
                                                                                                  
 conv1conv2d (Conv2D)           (None, 127, 127, 32  864         ['input_1[0][0]']                
                                )                                                                 
                                                                                                  
 conv1conv2dbn (BatchNormalizat  (None, 127, 127, 32  96         ['conv1conv2d[0][0]']            
 ion)                           )                                               

**Visualizing the RestNet16 architecture**

In [ ]:
dot_img_file = '/content/drive/MyDrive/Assignments/Assignment 4/Inception_ResNet_v2.png'
tf.keras.utils.plot_model(model, to_file=dot_img_file, show_shapes=True)

In [ ]:
tf.keras.models.save_model(model, '/content/drive/MyDrive/Assignments/Assignment 4/models/Inception-ResNet_v2.h5')

**Preprocessing the train and test images before training and validating the ResNet16 model**

In [ ]:
from keras.preprocessing.image import ImageDataGenerator
model.compile(optimizer='adam',loss=tf.keras.losses.SparseCategoricalCrossentropy(from_logits=True),metrics=['accuracy'])
#Applying Augmentaion on data to avoid overfitting
train_datagen = ImageDataGenerator(rescale = 1./255,shear_range = 0.2,zoom_range = 0.2,horizontal_flip = True)
val_datagen = ImageDataGenerator(rescale = 1./255)
test_datagen = ImageDataGenerator(rescale = 1./255)
training_set =train_datagen.flow_from_directory('/content/drive/MyDrive/Assignments/Assignment 3/Model_Training_Dataset/Train/',target_size = (256, 256),batch_size = 8,class_mode = 'binary')
val_set = val_datagen.flow_from_directory('/content/drive/MyDrive/Assignments/Assignment 3/Model_Training_Dataset/Val/',target_size = (256, 256),batch_size = 8,class_mode = 'binary')
test_set = test_datagen.flow_from_directory('/content/drive/MyDrive/Assignments/Assignment 3/Model_Training_Dataset/Test/',target_size = (256, 256),batch_size = 8,class_mode = 'binary')
type(training_set)

Found 3644 images belonging to 2 classes.
Found 1561 images belonging to 2 classes.
Found 520 images belonging to 2 classes.


keras.preprocessing.image.DirectoryIterator

In [ ]:
# filepath = "Inception_ResNet_v2_model.h5"
# checkpoint = ModelCheckpoint(filepath, monitor='val_acc',
#                         verbose=1, save_best_only=True, mode='max')

In [ ]:
# early = EarlyStopping(monitor="val_loss",
#                       mode="min",
#                       patience=4, restore_best_weights=True)
# callbacks_list = [checkpoint, early]

**Training the model**

In [ ]:
history = model.fit(training_set,steps_per_epoch = 10,epochs = 400,validation_data = val_set,validation_steps = 5)

Epoch 1/330
10/10 [==============================] - 15s 1s/step - loss: 0.0822 - accuracy: 0.9750 - val_loss: 0.0610 - val_accuracy: 1.0000
Epoch 2/330
10/10 [==============================] - 15s 2s/step - loss: 0.3141 - accuracy: 0.8750 - val_loss: 0.0775 - val_accuracy: 0.9500
Epoch 3/330
10/10 [==============================] - 15s 2s/step - loss: 0.1968 - accuracy: 0.9000 - val_loss: 0.0466 - val_accuracy: 0.9750
Epoch 4/330
10/10 [==============================] - 15s 2s/step - loss: 0.3941 - accuracy: 0.8250 - val_loss: 0.2792 - val_accuracy: 0.9250
Epoch 5/330
10/10 [==============================] - 15s 2s/step - loss: 0.2440 - accuracy: 0.8875 - val_loss: 0.4660 - val_accuracy: 0.8500
Epoch 6/330
10/10 [==============================] - 15s 2s/step - loss: 0.2180 - accuracy: 0.9125 - val_loss: 0.7804 - val_accuracy: 0.8750
Epoch 7/330
10/10 [==============================] - 14s 1s/step - loss: 0.1536 - accuracy: 0.9474 - val_loss: 0.1634 - val_accuracy: 0.9500
Epoch 8/330
1

**Variation of Train and Validation loss and accuracy with number of epochs**

In [ ]:
import matplotlib.pyplot as plt
plt.rcParams["figure.figsize"] = (18,9)

# plot loss during training
pyplot.subplot(211)
pyplot.title('Loss')
pyplot.plot(history.history['loss'], label='train')
pyplot.plot(history.history['val_loss'], label='val')
pyplot.legend()
# plot accuracy during training
pyplot.subplot(212)
pyplot.title('Accuracy')
pyplot.plot(history.history['accuracy'], label='train')
pyplot.plot(history.history['val_accuracy'], label='val')
pyplot.legend()
pyplot.savefig('/content/drive/MyDrive/Assignments/Assignment 4/TrainTest_LossAccuracy_Graph_Inception_ResNet_v2.png')
pyplot.show()

**Generating predictions and evaluation metrics on test set: Benign and Malignant**

In [ ]:
test_steps_per_epoch = np.math.ceil(test_set.samples / test_set.batch_size)

predictions = model.predict_generator(test_set, steps=test_steps_per_epoch)
# Get most likely class
predicted_classes = np.argmax(predictions, axis=1)

In [ ]:
true_classes = test_set.classes
class_labels = list(test_set.class_indices.keys())

In [ ]:
predicted_classes

In [ ]:
true_classes

**Generating model evaluation metrics like confusion matrix, precision, recall,F1 score**

**Train and Test accuracy have been generated earlier**

In [ ]:
import sklearn.metrics as metrics
report = metrics.classification_report(true_classes, predicted_classes, target_names=class_labels)
print(report)

In [ ]:
confusion_matrix = metrics.confusion_matrix(y_true=true_classes, y_pred=predicted_classes)

In [ ]:
len(true_classes)

In [ ]:
len(predicted_classes)

In [ ]:
confusion_matrix

In [ ]:
import seaborn as sns
import matplotlib.pyplot as plt

plt.rcParams["figure.figsize"] = (6,5)
ax= plt.subplot()
sns.heatmap(confusion_matrix, annot=True, fmt='g', ax=ax, annot_kws={"fontsize":18});  #annot=True to annotate cells, ftm='g' to disable scientific notation

# labels, title and ticks
ax.set_xlabel('Predicted labels', fontsize=18);
ax.set_ylabel('True labels', fontsize=18);
ax.set_title('Confusion Matrix',fontsize=22);
ax.xaxis.set_ticklabels(['Benign', 'Malignant'],fontsize=14);
ax.yaxis.set_ticklabels(['Benign', 'Malignant'],fontsize=14);

plt.savefig('/content/drive/MyDrive/Assignments/Assignment 4/Confusion_Matrix_Inception_ResNet_v2.png')

Val accuracy: 90.0%, Test accuracy: 86.4%